In [9]:
import pyrealsense2 as rs
import numpy as np
import cv2
import torch
import pandas as pd
import time

def get_filter(depth_colormap,variance):
    #RGB
    Rmax,Gmax,Bmax=255,255,255
    try:
        R=depth_colormap[0].mean()
        G=depth_colormap[1].mean()
        B=depth_colormap[2].mean()
        dmax=math.sqrt((Gmax-G)**2+(Bmax-B)**2)
        dmin=math.sqrt((G)**2+(B)**2)
        theta_1=math.atan(G/B)
        theta_2=math.atan((Gmax-G)/(Bmax-B))
        theta_3=math.asin((Rmax-R)/(dmax))
        theta_4=math.asin(R/dmin)
        #print(theta_1,theta_2,theta_3,theta_4)
        alpha=variance*math.cos(theta_3)
        gamma=variance*math.cos(theta_4)
        Rlow=R-variance*math.cos(theta_3)
        Glow=G-gamma*math.cos(theta_1)
        Blow=B-gamma*math.sin(theta_1)
        Rhigh=R+variance*math.sin(theta_4)
        Ghigh=G+alpha*math.sin(theta_2)
        Bhigh=B+alpha*math.cos(theta_2)
        return (int(Rhigh),int(Ghigh),int(Bhigh)),(int(Rlow),int(Glow),int(Blow))
    except :
        #print("error")
        return (18, 255, 255),(1, 190, 200)

def bincount_app(a):
    a2D = a.reshape(-1,a.shape[-1])
    col_range = (256, 256, 256) # generically : a2D.max(0)+1
    a1D = np.ravel_multi_index(a2D.T, col_range)
    return np.unravel_index(np.bincount(a1D).argmax(), col_range)

# Model
model = torch.hub.load('ultralytics/yolov5', 'yolov5s')  # or yolov5m, yolov5l, yolov5x, custom

x1=100
y1=100
light_blue = (1, 190, 200)
dark_blue = (18, 255, 255)
# Configure depth and color streams
pipeline = rs.pipeline()
config = rs.config()

# Get device product line for setting a supporting resolution
pipeline_wrapper = rs.pipeline_wrapper(pipeline)
pipeline_profile = config.resolve(pipeline_wrapper)
device = pipeline_profile.get_device()
device_product_line = str(device.get_info(rs.camera_info.product_line))

found_rgb = False
for s in device.sensors:
    if s.get_info(rs.camera_info.name) == 'RGB Camera':
        found_rgb = True
        break
if not found_rgb:
    print("The demo requires Depth camera with Color sensor")
    exit(0)

config.enable_stream(rs.stream.depth, 640, 480, rs.format.z16, 30)

if device_product_line == 'L500':
    config.enable_stream(rs.stream.color, 960, 540, rs.format.bgr8, 30)
else:
    config.enable_stream(rs.stream.color, 640, 480, rs.format.bgr8, 30)

# Start streaming
pipeline.start(config)
try:
    while True:
        # Wait for a coherent pair of frames: depth and color
        frames = pipeline.wait_for_frames()
        depth_frame = frames.get_depth_frame()
        color_frame = frames.get_color_frame()

        if not depth_frame or not color_frame:
            continue
        # Convert images to numpy arrays
        depth_image = np.asanyarray(depth_frame.get_data())
        color_image = np.asanyarray(color_frame.get_data())
        height, width= depth_image.shape
        #print(height, width)
        depth_image = depth_image[y1:height-y1+10, x1:width-130]
        height, width = depth_image.shape
        #print(height, width)
        #break
        # Apply colormap on depth image (image must be converted to 8-bit per pixel f0.irst)
        depth_colormap = cv2.applyColorMap(cv2.convertScaleAbs(depth_image, alpha=0.03), cv2.COLORMAP_JET)

        depth_colormap_dim = depth_colormap.shape
        color_colormap_dim = color_image.shape

        # If depth and color resolutions are different, resize color image to match depth image for display
        if depth_colormap_dim != color_colormap_dim:
            depth_colormap = cv2.resize(depth_colormap, dsize=(color_colormap_dim[1], color_colormap_dim[0]), interpolation=cv2.INTER_AREA)
            hsv_real = cv2.cvtColor(depth_colormap, cv2.COLOR_RGB2HSV)
            color_max,color_min=get_filter(depth_colormap,150)
            mask = cv2.inRange(hsv_real, light_blue, dark_blue)
            image = cv2.bitwise_and(depth_colormap, depth_colormap, mask=mask)
            mask = np.where((image==(0,0,0)).all(axis=2), 0, 255).astype(np.uint8)
            result = image.copy()
            result = cv2.cvtColor(result, cv2.COLOR_BGR2BGRA)
            result[:, :, 3] = mask
            result=cv2.addWeighted(color_image,0.5,image,0.7,0)
            results = model(color_image)
            frame_obj=[]
            contours=results.pandas().xyxy[0][results.pandas().xyxy[0]['confidence']>0.6]
            for x,y,w,h,name,confidence in zip(contours['xmin'].to_numpy().tolist(),contours['ymin'].to_numpy().tolist(),contours['xmax'].to_numpy().tolist(),contours['ymax'].to_numpy().tolist(),contours['name'].to_numpy().tolist(),contours['confidence'].to_numpy().tolist()):
                #depth = depth_frame.get_distance(int(x+(w-x)/2), int(y+(h-y)/2))
                #dx ,dy, dz = rs.rs2_deproject_pixel_to_point(color_intrin, [x,y], depth)
                #distance = math.sqrt(((dx)**2) + ((dy)**2) + ((dz)**2))
                minx=int(x+((w-x)/2))-5
                miny=int(y+((h-y)/2))-5
                maxx=minx+10
                maxy=miny+10
                frame_obj=[]
                for i in range(minx,maxx):
                    column=[]
                    for j in range(miny,maxy):
                        column.append(depth_frame.get_distance(i,j))
                    frame_obj.append(column)
                dis_frame=np.array(frame_obj)
                #distance=dis_frame[dis_frame<dis_frame.mean()*2.0].mean()
                distance=dis_frame.mean()
                cv2.rectangle(color_image,(int(x),int(y)),(int(w),int(h)),(0,255,0),2)
                cv2.rectangle(color_image,(int(x),int(y+10)),(int(w),int(y)-15),(0,255,0),-1)
                cv2.rectangle(color_image,(int(x),int(y)),(int(w),int(y)-15),(0,255,0),2)
                l=int(x+((w-x)/2))
                m=int(y+((h-y)/2))
                print(x,y,w,h,l,m)
                cv2.line(color_image, (l,m), (l+20,m), (0,0,255), 2)
                cv2.line(color_image, (l,m-20), (l,m), (0,255,0), 2)
                cv2.line(color_image, (l,m), (l-5,m+5), (255,0,0), 2)
                cv2.putText(color_image," "+name+" : "+str(round(confidence,1))+", dis: "+ str(round(distance,2)),(int(x),int(y)),cv2.FONT_HERSHEY_SIMPLEX,0.5,(255,255,255),2)
                #x line

                
            images = np.hstack((color_image,result,depth_colormap))
        else:
            images = np.hstack((color_image, depth_colormap))

        # Show images
        cv2.namedWindow('RealSense', cv2.WINDOW_AUTOSIZE)
        cv2.imshow('RealSense', images)
        cv2.waitKey(1)
        #if n>100:
        #    print("ready")
        #    cv2.imwrite('rgb_test_1.jpg', color_image)
        #    cv2.imwrite('depth_test_1.jpg', depth_colormap)
        #    break
finally:

    # Stop streaming
    pipeline.stop()

Using cache found in /home/robot/.cache/torch/hub/ultralytics_yolov5_master
YOLOv5 🚀 2022-4-25 torch 1.11.0+cu102 CUDA:0 (NVIDIA GeForce RTX 2080 Ti, 11017MiB)

Fusing layers... 
YOLOv5s summary: 213 layers, 7225885 parameters, 0 gradients
Adding AutoShape... 


39.87567138671875 0.0 640.0 479.7655029296875 339 239
56.92413330078125 0.0 640.0 478.38323974609375 348 239
57.047943115234375 0.0 640.0 478.81829833984375 348 239
58.001434326171875 0.0 640.0 479.46759033203125 349 239
58.318389892578125 0.0 640.0 479.30096435546875 349 239
55.791015625 0.0 640.0 479.38531494140625 347 239
37.15704345703125 0.0 640.0 480.0 338 240
56.986968994140625 0.0 640.0 479.0682373046875 348 239
55.684356689453125 0.0 640.0 479.5497131347656 347 239
38.186767578125 0.0 640.0 480.0 339 240
55.660888671875 0.0 640.0 478.17193603515625 347 239
37.013214111328125 0.0 640.0 479.77947998046875 338 239
56.158660888671875 0.0 640.0 478.62908935546875 348 239
54.199981689453125 0.0 640.0 478.7568359375 347 239
53.842193603515625 0.0 640.0 477.94140625 346 238
36.546173095703125 0.0 640.0 479.8534851074219 338 239
38.693572998046875 0.0 640.0 479.16436767578125 339 239
55.96075439453125 0.0 640.0 478.85540771484375 347 239
55.65228271484375 0.0 640.0 478.683837890625 347

294.9345703125 75.05250549316406 613.9315795898438 475.9351806640625 454 275
570.0060424804688 255.36688232421875 640.0 419.03179931640625 605 337
470.8974609375 408.6023864746094 639.842041015625 479.1702575683594 555 443
294.02423095703125 74.88740539550781 612.7919921875 476.39862060546875 453 275
570.1846313476562 255.36746215820312 640.0 417.7211608886719 605 336
470.8443908691406 408.895263671875 639.9334106445312 479.12408447265625 555 444
296.33551025390625 75.02507019042969 616.4185791015625 476.34130859375 456 275
569.463134765625 255.6538543701172 640.0 416.68218994140625 604 336
470.68975830078125 409.64996337890625 639.8991088867188 479.0809326171875 555 444
189.4010467529297 272.569580078125 228.06504821777344 326.1551513671875 208 299
296.54656982421875 74.23759460449219 612.4563598632812 476.32745361328125 454 275
569.3992309570312 255.64710998535156 640.0 413.6009521484375 604 334
470.6147155761719 409.72552490234375 639.9664916992188 479.2161865234375 555 444
189.3543

268.1292724609375 102.72694396972656 531.3651733398438 480.0 399 291
546.0052490234375 255.03819274902344 639.6883544921875 418.84735107421875 592 336
465.0534973144531 408.4339904785156 639.4266967773438 479.4381408691406 552 443
267.682373046875 103.91607666015625 529.7508544921875 480.0 398 291
548.20263671875 255.24627685546875 639.7642822265625 417.35162353515625 593 336
465.90911865234375 408.35858154296875 639.3378295898438 479.43902587890625 552 443
267.85345458984375 106.63630676269531 527.3771362304688 480.0 397 293
548.1884155273438 255.35218811035156 639.6688842773438 419.3525390625 593 337
467.2901611328125 408.53717041015625 639.3143310546875 479.33990478515625 553 443
268.72015380859375 108.58198547363281 525.0423583984375 480.0 396 294
547.7496337890625 255.217529296875 639.747802734375 418.24517822265625 593 336
465.3816223144531 408.26458740234375 639.27587890625 479.3671875 552 443
268.7014465332031 109.38487243652344 522.98486328125 480.0 395 294
548.3446655273438 2

290.52349853515625 152.2628631591797 496.63507080078125 480.0 393 316
548.0518798828125 255.17575073242188 639.6854248046875 416.2591247558594 593 335
471.0742492675781 408.86572265625 639.4432983398438 479.24578857421875 555 444
290.82940673828125 153.84288024902344 493.86279296875 480.0 392 316
547.8832397460938 255.19891357421875 639.6481323242188 415.12408447265625 593 335
289.6846923828125 155.1334228515625 494.1827392578125 479.43450927734375 391 317
547.62841796875 255.31028747558594 639.6766357421875 415.25244140625 593 335
189.48184204101562 272.84588623046875 228.28671264648438 326.11907958984375 208 299
290.9571838378906 156.4266357421875 491.5490417480469 479.54046630859375 391 317
547.5514526367188 255.6432342529297 639.6261596679688 418.68255615234375 593 337
472.22784423828125 409.3853454589844 639.3551635742188 479.3110046386719 555 444
291.2219543457031 156.93641662597656 492.3374328613281 479.21099853515625 391 318
548.5821533203125 255.40301513671875 639.619262695312

...

1.0345001220703125 6.6631622314453125 451.90142822265625 480.0 226 243
584.3975830078125 206.2603302001953 638.2623291015625 285.52362060546875 611 245
1.7711181640625 5.6891326904296875 451.7071838378906 480.0 226 242
584.5430297851562 206.37889099121094 638.3939819335938 285.4854431152344 611 245
514.0963134765625 196.9800567626953 637.9613037109375 360.59014892578125 576 278
2.1735382080078125 4.1661224365234375 453.2281494140625 480.0 227 242
584.4977416992188 206.22796630859375 638.3294067382812 284.8872985839844 611 245
514.1282348632812 196.92393493652344 637.9807739257812 361.84014892578125 576 279
1.4408721923828125 5.670440673828125 452.56591796875 480.0 227 242
584.40966796875 206.54034423828125 638.6104736328125 285.0276794433594 611 245
0.227813720703125 5.2544403076171875 451.716552734375 480.0 225 242
514.1387939453125 196.8869171142578 638.2755126953125 365.75 576 281
584.6084594726562 206.0963897705078 636.3869018554688 284.4173583984375 610 245
0.51116943359375 6.3550

584.70703125 206.5537567138672 638.396484375 285.044677734375 611 245
0.0 7.55633544921875 450.9676818847656 480.0 225 243
513.72314453125 196.82012939453125 638.1876220703125 359.43133544921875 575 278
0.3153228759765625 6.617767333984375 450.5482177734375 480.0 225 243
584.7791748046875 206.279052734375 637.8602294921875 284.984619140625 611 245
514.1162719726562 197.03659057617188 638.5524291992188 364.7143249511719 576 280
0.0 7.0626220703125 450.8244934082031 480.0 225 243
584.3309936523438 206.3430633544922 638.5111694335938 285.2488098144531 611 245
514.2476806640625 196.95632934570312 638.5458984375 366.2804870605469 576 281
584.6824340820312 206.33938598632812 638.2781372070312 285.48394775390625 611 245
0.2550811767578125 6.6644287109375 451.05743408203125 480.0 225 243
584.6966552734375 206.32797241210938 638.3922119140625 285.9296875 611 246
0.5010833740234375 5.023193359375 454.35650634765625 480.0 227 242
514.134033203125 196.9897003173828 637.598388671875 357.80792236328

584.74462890625 206.14500427246094 638.3070068359375 285.7071533203125 611 245
6.215606689453125 2.639373779296875 463.8752746582031 480.0 235 241
584.681884765625 206.39646911621094 638.355712890625 284.9989013671875 611 245
5.77142333984375 2.6936798095703125 465.96319580078125 480.0 235 241
514.6826782226562 197.27542114257812 637.7422485351562 361.0933532714844 576 279
584.67236328125 206.41555786132812 638.355224609375 285.20013427734375 611 245
6.6609344482421875 2.6620330810546875 463.26519775390625 480.0 234 241
584.8289794921875 206.33349609375 638.7694091796875 285.6938781738281 611 246
584.7777709960938 206.2408905029297 638.6699829101562 285.8305358886719 611 246
5.001495361328125 2.1871337890625 463.8031311035156 480.0 234 241
514.5927734375 197.07864379882812 637.0419921875 351.4781188964844 575 274
584.7656860351562 206.430419921875 638.7142944335938 285.5643005371094 611 245
514.6463623046875 196.91952514648438 637.967041015625 361.7296447753906 576 279
584.86328125 206

2.51202392578125 3.52593994140625 463.0279541015625 480.0 232 241
584.681396484375 206.24522399902344 638.4874267578125 285.4052734375 611 245
2.5084381103515625 2.6231689453125 462.974365234375 478.61328125 232 240
584.9059448242188 206.2671661376953 638.1355590820312 285.2724609375 611 245
584.7086181640625 206.33065795898438 638.439697265625 285.5039978027344 611 245
0.568450927734375 3.34234619140625 464.73486328125 479.3460693359375 232 241
584.5977172851562 206.10128784179688 637.9556274414062 284.9964599609375 611 245
3.0304107666015625 3.224578857421875 463.22503662109375 477.8887023925781 233 240
584.7452392578125 206.36279296875 638.0284423828125 285.5747375488281 611 245
2.300140380859375 1.3259735107421875 463.2283935546875 478.6094970703125 232 239
584.9428100585938 206.26300048828125 638.2786254882812 285.5467529296875 611 245
2.0860137939453125 4.1675262451171875 461.77752685546875 478.84967041015625 231 241
514.2139892578125 197.01548767089844 636.9874267578125 352.0191

KeyboardInterrupt: 